![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 15. <i>Korekta gramatyczna</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Ostatnią z omawianych przez nas technik stosowaną podczas wspomagania tłumaczenia jest korekta gramatyczna. Automatyczna korekta gramatyczna tekstu to ambitne zadanie odnalezienia możliwych błędów niezwiązanych bezpośrednio z pisownią. Są to między innymi:
* błędy gramatyczne
* źle użyte słowa
* złe połączenia wyrazowe
* błędy interpunkcyjne
* kolokwializmy
* redundancja (np. "tylko i wyłącznie")

Warto zwrócić uwagę, iż systemy do korekcji gramatycznej można traktować jako klasyfikatory binarne. Przyjmijmy, że odpowiedź pozytywna korektora to wykrycie błędu w tekście, natomiast negatywna - brak błędu. Wówczas rozróżniamy dwa typy pomyłek: false positive oraz false negative. False positive to tzw. "fałszywy alarm" - zbyt duża ich ilość spowoduje wydłużenie czasu pracy użytkownika przez konieczność analizowania zgłoszeń, które w istocie błędami nie są. Co jednak jeszcze gorsze, zbyt duża ilość false positives powoduje spadek zaufania użytkownika do systemu oraz drastyczny spadek satysfakcji z używania systemu. Te drugie błędy - false negatives - to z kolei faktyczne błędy w tekście, które nie zostały wyłapane przez system korekty. Stare polskie porzekadło głosi, że "czego oko nie widzi, tego sercu nie żal". Niestety jednak problem pojawia się, kiedy dostrzeże to jakieś inne oko... Wysoka liczba false negatives wprawdzie skraca czas korekty (sic!), ale odbywa się to kosztem jakości całego procesu. Idealnie zatem byłoby zminimalizować zarówno liczbę false positives, jak i false negatives. Jak jednak łatwo się domyślić, nie jest to zawsze możliwe. Korektor gramatyczny, który jest bardzo restrykcyjny i raportuje wiele błędów, będzie miał tendencję do popełniania false positives. Natomiast korektor bardziej pobłażliwy niechybnie popełni wiele false negatives. Co zatem jest ważniejsze? Praktyka wskazuje, że oba parametry mają podobną wagę, ale jednak odrobinę ważniejsze jest powstrzymanie się od false positives.

Do najbardziej popularnych narzędzi wspomagających korektę gramatyczną tekstu należą Grammarly oraz LanguageTool. Na dzisiejszych zajęciach zajmiemy się tym drugim. LanguageTool został pierwotnie napisany jako praca dyplomowa Daniela Nabera, a następnie intensywnie rozwijany wspólnie z Marcinem Miłkowskim. Aż do dziś projekt jest ciągle rozwijany, zwiększana jest liczba obsługiwanych języków oraz dokładność działania.

LanguageTool jest systemem opartym na regułach. W dobie wszechobecnej sztucznej inteligencji opartej na uczeniu maszynowym rozwiązanie to wydaje się nieco przestarzałe. Jednak to właśnie reguły stanowią o sile LanguageToola - pozwalają one na zwiększenie precyzji korektora poprzez minimalizację false positives. Warto wspomnieć, iż liczne reguły LanguageToola dotyczą również korekty pisowni. Czyni to z LanguageToola kompletne narzędzie do korekty tekstu. Polecam przejrzenie zestawu reguł LanguageToola dla języka angielskiego: https://community.languagetool.org/rule/list?lang=en

Czas uruchomić to narzędzie. Skorzystajmy z Pythona.

In [14]:
!pip install language_tool_python

Następnie możemy użyć LanguageToola w programie Pythonowym: (przykład zaczerpnięty z oficjalnego tutoriala: https://pypi.org/project/language-tool-python/)

In [15]:
import language_tool_python
import pprint
tool = language_tool_python.LanguageTool('en-US') 

text = 'A sentence with a error in the Hitchhiker’s Guide tot he Galaxy'

pp = pprint.PrettyPrinter(depth=2)
errors = tool.check(text)
pp.pprint(errors)

[Match({'ruleId': 'EN_A_VS_AN', 'message': 'Use “an” instead of ‘a’ if the following word starts with a vowel sound, e.g. ‘an article’, ‘an hour’.', 'replacements': ['an'], 'offsetInContext': 16, 'context': 'A sentence with a error in the Hitchhiker’s Guide tot he ...', 'offset': 16, 'errorLength': 1, 'category': 'MISC', 'ruleIssueType': 'misspelling', 'sentence': "A sentence with a error in the Hitchhiker's Guide tot he Galaxy"}),
 Match({'ruleId': 'TOT_HE', 'message': 'Did you mean “to the”?', 'replacements': ['to the'], 'offsetInContext': 43, 'context': '... with a error in the Hitchhiker’s Guide tot he Galaxy', 'offset': 50, 'errorLength': 6, 'category': 'TYPOS', 'ruleIssueType': 'misspelling', 'sentence': "A sentence with a error in the Hitchhiker's Guide tot he Galaxy"})]


Przeanalizujmy format zwracanego wyniku. Otrzymujemy listę obiektów Match - zawiadomień o potencjalnym błędzie. Razem z każdym błędem otrzymujemy m.in. identyfikator użytej reguły, opis błędu, rekomendancję poprawy, kontekst.

### Ćwiczenie 1: Użyj LanguageTool do znalezienia jak największej liczby prawdziwych błędów na swoim ulubionym portalu internetowym. Skorzystaj z poznanych wcześniej technik web scrapingu. Uwaga - LanguageTool najprawdopodobniej oznaczy nazwy własne jako literówki - ten typ błędu nie powinien być brany pod uwagę.

In [16]:
import requests
from bs4 import BeautifulSoup

def fetch_webpage_content(url):
    response = requests.get(url)
    response.raise_for_status()  # Raise an exception for HTTP errors
    soup = BeautifulSoup(response.content, 'html.parser')
    return soup.get_text()

In [19]:
def find_errors(website_url):
    tool = language_tool_python.LanguageTool('pl-PL')
    text = fetch_webpage_content(website_url)

    errors = tool.check(text)

    filtered_errors = [error for error in errors if error.ruleId != 'UPPERCASE_SENTENCE_START']
    return filtered_errors

In [20]:
website_url = 'https://wmi.amu.edu.pl/'
pp = pprint.PrettyPrinter(depth=2)
pp.pprint(find_errors(website_url))

[Match({'ruleId': 'WHITESPACE_RULE', 'message': 'Prawdopodobna literówka: wiele spacji z rzędu', 'replacements': [' '], 'offsetInContext': 43, 'context': '...rypty w Twojej przeglądarce znajdziesz\r                  tutaj \r                             Prze...', 'offset': 325, 'errorLength': 17, 'category': 'TYPOGRAPHY', 'ruleIssueType': 'whitespace', 'sentence': 'Brak obsługi JavaScript\nDo pełnej funkcjonalności strony potrzebujesz włączonej obsługi skryptów. Instrukcje, które pozwolą Ci włączyć skrypty w Twojej przeglądarce znajdziesz\r\n                 tutaj'}),
 Match({'ruleId': 'WHITESPACE_RULE', 'message': 'Prawdopodobna literówka: wiele spacji z rzędu', 'replacements': [' '], 'offsetInContext': 43, 'context': '...ce znajdziesz\r                  tutaj \r                             Przejdź do TreśćPrzejdź do M...', 'offset': 350, 'errorLength': 16, 'category': 'TYPOGRAPHY', 'ruleIssueType': 'whitespace', 'sentence': 'Brak obsługi JavaScript\nDo pełnej funkcjonalności strony po

### Ćwiczenie 2: Napisz skrypt, który poszuka błędów w komentarzach klasy Javowej (zwykłych // oraz w javadocach). Uruchom ten skrypt na źródłach wybranego opensourcowego projektu w Javie.

In [27]:
import re

def extract_comments(java_code):
    single_line_comments = re.findall(r'//.*', java_code)
    multi_line_comments = re.findall(r'/\*\*[\s\S]*?\*/', java_code)
    comments = single_line_comments + multi_line_comments
    return comments

In [28]:
def correct_java_grammar(java_file_content):
    # Ekstrakcja komentarzy
    comments = extract_comments(java_file_content)
    text_to_check = '\n'.join(comments)
    
    # Użycie LanguageTool do analizy komentarzy
    tool = language_tool_python.LanguageTool('en-US')  # Ustawiamy język na angielski
    errors = tool.check(text_to_check)
    
    # Wyświetlenie wyników
    pp = pprint.PrettyPrinter(depth=2)
    pp.pprint(errors)
    
    return errors

In [29]:
java_file = """/*
 * Copyright (c) 2016-present, RxJava Contributors.
 *
 * Licensed under the Apache License, Version 2.0 (the "License"); you may not use this file except in
 * compliance with the License. You may obtain a copy of the License at
 *
 * http://www.apache.org/licenses/LICENSE-2.0
 *
 * Unless required by applicable law or agreed to in writing, software distributed under the License is
 * distributed on an "AS IS" BASIS, WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied. See
 * the License for the specific language governing permissions and limitations under the License.
 */

package io.reactivex.rxjava3.flowables;

import java.util.Objects;
import java.util.concurrent.TimeUnit;

import org.reactivestreams.*;

import io.reactivex.rxjava3.annotations.*;
import io.reactivex.rxjava3.core.*;
import io.reactivex.rxjava3.disposables.Disposable;
import io.reactivex.rxjava3.functions.Consumer;
import io.reactivex.rxjava3.internal.functions.*;
import io.reactivex.rxjava3.internal.operators.flowable.*;
import io.reactivex.rxjava3.internal.util.ConnectConsumer;
import io.reactivex.rxjava3.plugins.RxJavaPlugins;
import io.reactivex.rxjava3.schedulers.Schedulers;

/**
 * A {@code ConnectableFlowable} resembles an ordinary {@link Flowable}, except that it does not begin
 * emitting items when it is subscribed to, but only when its {@link #connect} method is called. In this way you
 * can wait for all intended {@link Subscriber}s to {@link Flowable#subscribe} to the {@code Flowable}
 * before the {@code Flowable} begins emitting items.
 * <p>
 * <img width="640" height="510" src="https://github.com/ReactiveX/RxJava/wiki/images/rx-operators/publishConnect.v3.png" alt="">
 * <p>
 * When the upstream terminates, the {@code ConnectableFlowable} remains in this terminated state and,
 * depending on the actual underlying implementation, relays cached events to late {@code Subscriber}s.
 * In order to reuse and restart this {@code ConnectableFlowable}, the {@link #reset()} method has to be called.
 * When called, this {@code ConnectableFlowable} will appear as fresh, unconnected source to new {@code Subscriber}s.
 * Disposing the connection will reset the {@code ConnectableFlowable} to its fresh state and there is no need to call
 * {@code reset()} in this case.
 * <p>
 * Note that although {@link #connect()} and {@link #reset()} are safe to call from multiple threads, it is recommended
 * a dedicated thread or business logic manages the connection or resetting of a {@code ConnectableFlowable} so that
 * there is no unwanted signal loss due to early {@code connect()} or {@code reset()} calls while {@code Subscriber}s are
 * still being subscribed to to this {@code ConnectableFlowable} to receive signals from the get go.
 * <p>
 * @see <a href="https://github.com/ReactiveX/RxJava/wiki/Connectable-Observable-Operators">RxJava Wiki: Connectable Observable Operators</a>
 * @param <T>
 *          the type of items emitted by the {@code ConnectableFlowable}
 * @since 2.0.0
 */
public abstract class ConnectableFlowable<T> extends Flowable<T> {

    /**
     * Instructs the {@code ConnectableFlowable} to begin emitting the items from its underlying
     * {@link Flowable} to its {@link Subscriber}s.
     * <dl>
     *  <dt><b>Scheduler:</b></dt>
     *  <dd>The behavior is determined by the implementor of this abstract class.</dd>
     * </dl>
     *
     * @param connection
     *          the action that receives the connection subscription before the subscription to source happens
     *          allowing the caller to synchronously disconnect a synchronous source
     * @throws NullPointerException if {@code connection} is {@code null}
     * @see <a href="http://reactivex.io/documentation/operators/connect.html">ReactiveX documentation: Connect</a>
     */
    @SchedulerSupport(SchedulerSupport.NONE)
    public abstract void connect(@NonNull Consumer<? super Disposable> connection);

    /**
     * Resets this {@code ConnectableFlowable} into its fresh state if it has terminated.
     * <p>
     * Calling this method on a fresh or active {@code ConnectableFlowable} has no effect.
     * <dl>
     *  <dt><b>Scheduler:</b></dt>
     *  <dd>The behavior is determined by the implementor of this abstract class.</dd>
     * </dl>
     * @since 3.0.0
     */
    @SchedulerSupport(SchedulerSupport.NONE)
    public abstract void reset();

    /**
     * Instructs the {@code ConnectableFlowable} to begin emitting the items from its underlying
     * {@link Flowable} to its {@link Subscriber}s.
     * <p>
     * To disconnect from a synchronous source, use the {@link #connect(io.reactivex.rxjava3.functions.Consumer)} method.
     * <dl>
     *  <dt><b>Scheduler:</b></dt>
     *  <dd>The behavior is determined by the implementor of this abstract class.</dd>
     * </dl>
     *
     * @return the subscription representing the connection
     * @see <a href="http://reactivex.io/documentation/operators/connect.html">ReactiveX documentation: Connect</a>
     */
    @NonNull
    @SchedulerSupport(SchedulerSupport.NONE)
    public final Disposable connect() {
        ConnectConsumer cc = new ConnectConsumer();
        connect(cc);
        return cc.disposable;
    }

    /**
     * Returns a {@link Flowable} that stays connected to this {@code ConnectableFlowable} as long as there
     * is at least one subscription to this {@code ConnectableFlowable}.
     * <dl>
     *  <dt><b>Backpressure:</b></dt>
     *  <dd>The operator itself doesn't interfere with backpressure which is determined by the upstream
     *  {@code ConnectableFlowable}'s backpressure behavior.</dd>
     *  <dt><b>Scheduler:</b></dt>
     *  <dd>This {@code refCount} overload does not operate on any particular {@link Scheduler}.</dd>
     * </dl>
     * @return the new {@code Flowable} instance
     * @see <a href="http://reactivex.io/documentation/operators/refcount.html">ReactiveX documentation: RefCount</a>
     * @see #refCount(int)
     * @see #refCount(long, TimeUnit)
     * @see #refCount(int, long, TimeUnit)
     */
    @NonNull
    @CheckReturnValue
    @SchedulerSupport(SchedulerSupport.NONE)
    @BackpressureSupport(BackpressureKind.PASS_THROUGH)
    public Flowable<T> refCount() {
        return RxJavaPlugins.onAssembly(new FlowableRefCount<>(this));
    }

    /**
     * Connects to the upstream {@code ConnectableFlowable} if the number of subscribed
     * subscriber reaches the specified count and disconnect if all subscribers have unsubscribed.
     * <dl>
     *  <dt><b>Backpressure:</b></dt>
     *  <dd>The operator itself doesn't interfere with backpressure which is determined by the upstream
     *  {@code ConnectableFlowable}'s backpressure behavior.</dd>
     *  <dt><b>Scheduler:</b></dt>
     *  <dd>This {@code refCount} overload does not operate on any particular {@link Scheduler}.</dd>
     * </dl>
     * <p>History: 2.1.14 - experimental
     * @param subscriberCount the number of subscribers required to connect to the upstream
     * @return the new {@link Flowable} instance
     * @throws IllegalArgumentException if {@code subscriberCount} is non-positive
     * @since 2.2
     */
    @CheckReturnValue
    @SchedulerSupport(SchedulerSupport.NONE)
    @BackpressureSupport(BackpressureKind.PASS_THROUGH)
    @NonNull
    public final Flowable<T> refCount(int subscriberCount) {
        return refCount(subscriberCount, 0, TimeUnit.NANOSECONDS, Schedulers.trampoline());
    }

    /**
     * Connects to the upstream {@code ConnectableFlowable} if the number of subscribed
     * subscriber reaches 1 and disconnect after the specified
     * timeout if all subscribers have unsubscribed.
     * <dl>
     *  <dt><b>Backpressure:</b></dt>
     *  <dd>The operator itself doesn't interfere with backpressure which is determined by the upstream
     *  {@code ConnectableFlowable}'s backpressure behavior.</dd>
     *  <dt><b>Scheduler:</b></dt>
     *  <dd>This {@code refCount} overload operates on the {@code computation} {@link Scheduler}.</dd>
     * </dl>
     * <p>History: 2.1.14 - experimental
     * @param timeout the time to wait before disconnecting after all subscribers unsubscribed
     * @param unit the time unit of the timeout
     * @return the new {@link Flowable} instance
     * @throws NullPointerException if {@code unit} is {@code null}
     * @see #refCount(long, TimeUnit, Scheduler)
     * @since 2.2
     */
    @CheckReturnValue
    @SchedulerSupport(SchedulerSupport.COMPUTATION)
    @BackpressureSupport(BackpressureKind.PASS_THROUGH)
    @NonNull
    public final Flowable<T> refCount(long timeout, @NonNull TimeUnit unit) {
        return refCount(1, timeout, unit, Schedulers.computation());
    }

    /**
     * Connects to the upstream {@code ConnectableFlowable} if the number of subscribed
     * subscriber reaches 1 and disconnect after the specified
     * timeout if all subscribers have unsubscribed.
     * <dl>
     *  <dt><b>Backpressure:</b></dt>
     *  <dd>The operator itself doesn't interfere with backpressure which is determined by the upstream
     *  {@code ConnectableFlowable}'s backpressure behavior.</dd>
     *  <dt><b>Scheduler:</b></dt>
     *  <dd>This {@code refCount} overload operates on the specified {@link Scheduler}.</dd>
     * </dl>
     * <p>History: 2.1.14 - experimental
     * @param timeout the time to wait before disconnecting after all subscribers unsubscribed
     * @param unit the time unit of the timeout
     * @param scheduler the target scheduler to wait on before disconnecting
     * @return the new {@link Flowable} instance
     * @throws NullPointerException if {@code unit} or {@code scheduler} is {@code null}
     * @since 2.2
     */
    @CheckReturnValue
    @SchedulerSupport(SchedulerSupport.CUSTOM)
    @BackpressureSupport(BackpressureKind.PASS_THROUGH)
    @NonNull
    public final Flowable<T> refCount(long timeout, @NonNull TimeUnit unit, @NonNull Scheduler scheduler) {
        return refCount(1, timeout, unit, scheduler);
    }

    /**
     * Connects to the upstream {@code ConnectableFlowable} if the number of subscribed
     * subscriber reaches the specified count and disconnect after the specified
     * timeout if all subscribers have unsubscribed.
     * <dl>
     *  <dt><b>Backpressure:</b></dt>
     *  <dd>The operator itself doesn't interfere with backpressure which is determined by the upstream
     *  {@code ConnectableFlowable}'s backpressure behavior.</dd>
     *  <dt><b>Scheduler:</b></dt>
     *  <dd>This {@code refCount} overload operates on the {@code computation} {@link Scheduler}.</dd>
     * </dl>
     * <p>History: 2.1.14 - experimental
     * @param subscriberCount the number of subscribers required to connect to the upstream
     * @param timeout the time to wait before disconnecting after all subscribers unsubscribed
     * @param unit the time unit of the timeout
     * @return the new {@link Flowable} instance
     * @throws NullPointerException if {@code unit} is {@code null}
     * @throws IllegalArgumentException if {@code subscriberCount} is non-positive
     * @see #refCount(int, long, TimeUnit, Scheduler)
     * @since 2.2
     */
    @CheckReturnValue
    @SchedulerSupport(SchedulerSupport.COMPUTATION)
    @BackpressureSupport(BackpressureKind.PASS_THROUGH)
    @NonNull
    public final Flowable<T> refCount(int subscriberCount, long timeout, @NonNull TimeUnit unit) {
        return refCount(subscriberCount, timeout, unit, Schedulers.computation());
    }

    /**
     * Connects to the upstream {@code ConnectableFlowable} if the number of subscribed
     * subscriber reaches the specified count and disconnect after the specified
     * timeout if all subscribers have unsubscribed.
     * <dl>
     *  <dt><b>Backpressure:</b></dt>
     *  <dd>The operator itself doesn't interfere with backpressure which is determined by the upstream
     *  {@code ConnectableFlowable}'s backpressure behavior.</dd>
     *  <dt><b>Scheduler:</b></dt>
     *  <dd>This {@code refCount} overload operates on the specified {@link Scheduler}.</dd>
     * </dl>
     * <p>History: 2.1.14 - experimental
     * @param subscriberCount the number of subscribers required to connect to the upstream
     * @param timeout the time to wait before disconnecting after all subscribers unsubscribed
     * @param unit the time unit of the timeout
     * @param scheduler the target scheduler to wait on before disconnecting
     * @return the new {@link Flowable} instance
     * @throws NullPointerException if {@code unit} or {@code scheduler} is {@code null}
     * @throws IllegalArgumentException if {@code subscriberCount} is non-positive
     * @since 2.2
     */
    @CheckReturnValue
    @SchedulerSupport(SchedulerSupport.CUSTOM)
    @BackpressureSupport(BackpressureKind.PASS_THROUGH)
    @NonNull
    public final Flowable<T> refCount(int subscriberCount, long timeout, @NonNull TimeUnit unit, @NonNull Scheduler scheduler) {
        ObjectHelper.verifyPositive(subscriberCount, "subscriberCount");
        Objects.requireNonNull(unit, "unit is null");
        Objects.requireNonNull(scheduler, "scheduler is null");
        return RxJavaPlugins.onAssembly(new FlowableRefCount<>(this, subscriberCount, timeout, unit, scheduler));
    }

    /**
     * Returns a {@link Flowable} that automatically connects (at most once) to this {@code ConnectableFlowable}
     * when the first {@link Subscriber} subscribes.
     * <p>
     * <img width="640" height="392" src="https://raw.github.com/wiki/ReactiveX/RxJava/images/rx-operators/autoConnect.f.png" alt="">
     * <p>
     * The connection happens after the first subscription and happens at most once
     * during the lifetime of the returned {@code Flowable}. If this {@code ConnectableFlowable}
     * terminates, the connection is never renewed, no matter how {@code Subscriber}s come
     * and go. Use {@link #refCount()} to renew a connection or dispose an active
     * connection when all {@code Subscriber}s have cancelled their {@link Subscription}s.
     * <p>
     * This overload does not allow disconnecting the connection established via
     * {@link #connect(Consumer)}. Use the {@link #autoConnect(int, Consumer)} overload
     * to gain access to the {@link Disposable} representing the only connection.
     * <dl>
     *  <dt><b>Backpressure:</b></dt>
     *  <dd>The operator itself doesn't interfere with backpressure which is determined by
     *  the upstream {@code ConnectableFlowable}'s behavior.</dd>
     *  <dt><b>Scheduler:</b></dt>
     *  <dd>{@code autoConnect} does not operate by default on a particular {@link Scheduler}.</dd>
     * </dl>
     *
     * @return a new {@code Flowable} instance that automatically connects to this {@code ConnectableFlowable}
     *         when the first {@code Subscriber} subscribes
     * @see #refCount()
     * @see #autoConnect(int, Consumer)
     */
    @NonNull
    @CheckReturnValue
    @BackpressureSupport(BackpressureKind.PASS_THROUGH)
    @SchedulerSupport(SchedulerSupport.NONE)
    public Flowable<T> autoConnect() {
        return autoConnect(1);
    }
    /**
     * Returns a {@link Flowable} that automatically connects (at most once) to this {@code ConnectableFlowable}
     * when the specified number of {@link Subscriber}s subscribe to it.
     * <p>
     * <img width="640" height="392" src="https://raw.github.com/wiki/ReactiveX/RxJava/images/rx-operators/autoConnect.f.png" alt="">
     * <p>
     * The connection happens after the given number of subscriptions and happens at most once
     * during the lifetime of the returned {@code Flowable}. If this {@code ConnectableFlowable}
     * terminates, the connection is never renewed, no matter how {@code Subscriber}s come
     * and go. Use {@link #refCount()} to renew a connection or dispose an active
     * connection when all {@code Subscriber}s have cancelled their {@link Subscription}s.
     * <p>
     * This overload does not allow disconnecting the connection established via
     * {@link #connect(Consumer)}. Use the {@link #autoConnect(int, Consumer)} overload
     * to gain access to the {@link Disposable} representing the only connection.
     * <dl>
     *  <dt><b>Backpressure:</b></dt>
     *  <dd>The operator itself doesn't interfere with backpressure which is determined by
     *  the upstream {@code ConnectableFlowable}'s behavior.</dd>
     *  <dt><b>Scheduler:</b></dt>
     *  <dd>{@code autoConnect} does not operate by default on a particular {@link Scheduler}.</dd>
     * </dl>
     *
     * @param numberOfSubscribers the number of subscribers to await before calling connect
     *                            on the {@code ConnectableFlowable}. A non-positive value indicates
     *                            an immediate connection.
     * @return a new {@code Flowable} instance that automatically connects to this {@code ConnectableFlowable}
     *         when the specified number of {@code Subscriber}s subscribe to it
     */
    @NonNull
    @CheckReturnValue
    @BackpressureSupport(BackpressureKind.PASS_THROUGH)
    @SchedulerSupport(SchedulerSupport.NONE)
    public Flowable<T> autoConnect(int numberOfSubscribers) {
        return autoConnect(numberOfSubscribers, Functions.emptyConsumer());
    }

    /**
     * Returns a {@link Flowable} that automatically connects (at most once) to this {@code ConnectableFlowable}
     * when the specified number of {@link Subscriber}s subscribe to it and calls the
     * specified callback with the {@link Disposable} associated with the established connection.
     * <p>
     * <img width="640" height="392" src="https://raw.github.com/wiki/ReactiveX/RxJava/images/rx-operators/autoConnect.f.png" alt="">
     * <p>
     * The connection happens after the given number of subscriptions and happens at most once
     * during the lifetime of the returned {@code Flowable}. If this {@code ConnectableFlowable}
     * terminates, the connection is never renewed, no matter how {@code Subscriber}s come
     * and go. Use {@link #refCount()} to renew a connection or dispose an active
     * connection when all {@code Subscriber}s have cancelled their {@link Subscription}s.
     * <dl>
     *  <dt><b>Backpressure:</b></dt>
     *  <dd>The operator itself doesn't interfere with backpressure which is determined by
     *  the upstream {@code ConnectableFlowable}'s behavior.</dd>
     *  <dt><b>Scheduler:</b></dt>
     *  <dd>{@code autoConnect} does not operate by default on a particular {@link Scheduler}.</dd>
     * </dl>
     *
     * @param numberOfSubscribers the number of subscribers to await before calling connect
     *                            on the {@code ConnectableFlowable}. A non-positive value indicates
     *                            an immediate connection.
     * @param connection the callback {@link Consumer} that will receive the {@code Disposable} representing the
     *                   established connection
     * @return a new {@code Flowable} instance that automatically connects to this {@code ConnectableFlowable}
     *         when the specified number of {@code Subscriber}s subscribe to it and calls the
     *         specified callback with the {@code Disposable} associated with the established connection
     * @throws NullPointerException if {@code connection} is {@code null}
     */
    @NonNull
    @CheckReturnValue
    @BackpressureSupport(BackpressureKind.PASS_THROUGH)
    @SchedulerSupport(SchedulerSupport.NONE)
    public Flowable<T> autoConnect(int numberOfSubscribers, @NonNull Consumer<? super Disposable> connection) {
        Objects.requireNonNull(connection, "connection is null");
        if (numberOfSubscribers <= 0) {
            this.connect(connection);
            return RxJavaPlugins.onAssembly(this);
        }
        return RxJavaPlugins.onAssembly(new FlowableAutoConnect<>(this, numberOfSubscribers, connection));
    }
}"""

correct_java_grammar(java_file)

[Match({'ruleId': 'EN_UNPAIRED_QUOTES', 'message': 'Unpaired symbol: ‘"’ seems to be missing', 'replacements': [], 'offsetInContext': 43, 'context': '...mages/rx-operators/publishConnect.v3.png" alt=""> //github.com/ReactiveX/RxJava/w...', 'offset': 114, 'errorLength': 1, 'category': 'PUNCTUATION', 'ruleIssueType': 'typographical', 'sentence': '//www.apache.org/licenses/LICENSE-2.0\n//github.com/ReactiveX/RxJava/wiki/images/rx-operators/publishConnect.v3.png" alt="">\n//github.com/ReactiveX/RxJava/wiki/Connectable-Observable-Operators">RxJava Wiki: Connectable Observable Operators</a>\n//reactivex.io/documentation/operators/connect.html">ReactiveX documentation: Connect</a>\n//reactivex.io/documentation/operators/connect.html">ReactiveX documentation: Connect</a>\n//reactivex.io/documentation/operators/refcount.html">ReactiveX documentation: RefCount</a>\n//raw.github.com/wiki/ReactiveX/RxJava/images/rx-operators/autoConnect.f.png" alt="">\n//raw.github.com/wiki/ReactiveX/RxJava/images

[Match({'ruleId': 'EN_UNPAIRED_QUOTES', 'message': 'Unpaired symbol: ‘"’ seems to be missing', 'replacements': [], 'offsetInContext': 43, 'context': '...mages/rx-operators/publishConnect.v3.png" alt=""> //github.com/ReactiveX/RxJava/w...', 'offset': 114, 'errorLength': 1, 'category': 'PUNCTUATION', 'ruleIssueType': 'typographical', 'sentence': '//www.apache.org/licenses/LICENSE-2.0\n//github.com/ReactiveX/RxJava/wiki/images/rx-operators/publishConnect.v3.png" alt="">\n//github.com/ReactiveX/RxJava/wiki/Connectable-Observable-Operators">RxJava Wiki: Connectable Observable Operators</a>\n//reactivex.io/documentation/operators/connect.html">ReactiveX documentation: Connect</a>\n//reactivex.io/documentation/operators/connect.html">ReactiveX documentation: Connect</a>\n//reactivex.io/documentation/operators/refcount.html">ReactiveX documentation: RefCount</a>\n//raw.github.com/wiki/ReactiveX/RxJava/images/rx-operators/autoConnect.f.png" alt="">\n//raw.github.com/wiki/ReactiveX/RxJava/images